In [1]:
from __future__ import division
import pandas as pd
import warnings
warnings.filterwarnings('ignore')
import numpy as np

from difflib import SequenceMatcher

import seaborn as sns
import matplotlib.pyplot as plt
%matplotlib inline

from sklearn.preprocessing import LabelEncoder
from sklearn.pipeline import Pipeline

#import decisiontreeclassifier
from sklearn import tree
from sklearn.tree import DecisionTreeClassifier
#import logisticregression classifier
from sklearn.linear_model import LogisticRegression
import statsmodels.api as sm
#import knn classifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn import svm
from sklearn.multiclass import OneVsRestClassifier
from sklearn.svm import SVC
from sklearn.ensemble import RandomForestClassifier

#for validating your classification model
from sklearn.cross_validation import train_test_split
from sklearn.cross_validation import cross_val_score
from sklearn import metrics
from sklearn.metrics import roc_curve, auc

# feature selection
from sklearn.feature_selection import RFE
from sklearn.ensemble import ExtraTreesClassifier
from sklearn.feature_selection import SelectKBest
from sklearn.feature_selection import chi2

C:\Users\MohammadhosseinAmini\AppData\Local\conda\conda\envs\py36\lib\site-packages\sklearn\ensemble\weight_boosting.py:29: DeprecationWarning: numpy.core.umath_tests is an internal NumPy module and should not be imported. It will be removed in a future NumPy release.
  from numpy.core.umath_tests import inner1d
C:\Users\MohammadhosseinAmini\AppData\Local\conda\conda\envs\py36\lib\site-packages\sklearn\cross_validation.py:41: DeprecationWarning: This module was deprecated in version 0.18 in favor of the model_selection module into which all the refactored classes and functions are moved. Also note that the interface of the new CV iterators are different from that of this module. This module will be removed in 0.20.
  "This module will be removed in 0.20.", DeprecationWarning)


In [2]:
df=pd.read_csv('fda2.csv',low_memory=False)
df.loc[df['reporter_country'].isnull(), 'reporter_country']='country not specified'
df.head()

primaryid  drug_seq      caseid                              indi_pt  \
0  100033001         1  10003300.0                         osteoporosis   
1  100033001         1  10003300.0                         osteoporosis   
2  100033061         1  10003306.0  product used for unknown indication   
3  100033062         1  10003306.0  product used for unknown indication   
4  100033072         2  10003307.0           connective tissue disorder   

   drugname   age  gndr_cod  wt       reporter_country  de  lt  ho  ds  ca  \
0    boniva  77.0       0.0 NaN                     us   0   0   0   1   0   
1    boniva  77.0       0.0 NaN                     us   0   0   0   1   0   
2       NaN  68.0       0.0 NaN                     us   0   0   0   0   0   
3  letairis  68.0       0.0 NaN                     us   0   0   0   0   0   
4  letairis   NaN       NaN NaN  country not specified   0   0   0   0   0   

   ri  ot           pt  
0   0   0   arthralgia  
1   0   0     headache  
2   0   0        cough  
3   0   0        cough  
4   0   0  rhinorrhoea

In [3]:
df['drugbank_ID']=None
df.head()

primaryid  drug_seq      caseid                              indi_pt  \
0  100033001         1  10003300.0                         osteoporosis   
1  100033001         1  10003300.0                         osteoporosis   
2  100033061         1  10003306.0  product used for unknown indication   
3  100033062         1  10003306.0  product used for unknown indication   
4  100033072         2  10003307.0           connective tissue disorder   

   drugname   age  gndr_cod  wt       reporter_country  de  lt  ho  ds  ca  \
0    boniva  77.0       0.0 NaN                     us   0   0   0   1   0   
1    boniva  77.0       0.0 NaN                     us   0   0   0   1   0   
2       NaN  68.0       0.0 NaN                     us   0   0   0   0   0   
3  letairis  68.0       0.0 NaN                     us   0   0   0   0   0   
4  letairis   NaN       NaN NaN  country not specified   0   0   0   0   0   

   ri  ot           pt drugbank_ID  
0   0   0   arthralgia        None  
1   0   0     headache        None  
2   0   0        cough        None  
3   0   0        cough        None  
4   0   0  rhinorrhoea        None

In [4]:
df_drugbank=pd.read_excel('drugbank.xlsx')
df_drugbank.head()

drugbank-id                 name  \
0     DB00001            Lepirudin   
1     DB00002            Cetuximab   
2     DB00003         Dornase alfa   
3     DB00004  Denileukin diftitox   
4     DB00005           Etanercept   

                                         description   cas-number        unii  \
0  Lepirudin is identical to natural hirudin exce...  138068-37-8  Y43GF64R34   
1  Cetuximab is an epidermal growth factor recept...  205923-56-4  PQX0D8J21J   
2  Dornase alfa is a biosynthetic form of human d...  143831-71-4  953A26OA1Y   
3  A recombinant DNA-derived cytotoxic protein co...  173146-27-5  25E79B5CTM   
4  Dimeric fusion protein consisting of the extra...  185243-69-0  OP401G7OJC   

    state                   groups  \
0  liquid                 approved   
1  liquid                 approved   
2  liquid                 approved   
3  liquid  approvedinvestigational   
4  liquid  approvedinvestigational   

                                  general-references  \
0  16244762Smythe MA, Stephens JL, Koerber JM, Ma...   
1  10480573Hosokawa N, Yamamoto S, Uehara Y, Hori...   
2  8792953Cramer GW, Bosso JA: The role of dornas...   
3  17187516Turturro F: Denileukin diftitox: a bio...   
4  Linkhttp://www.genome.jp/dbget-bin/www_bget?D0...   

                                 synthesis-reference  \
0                                                NaN   
1                                                NaN   
2                                                NaN   
3                                                NaN   
4  Timothy D. Osslund, Christi L. Clogston, Shon ...   

                                          indication          ...           \
0  For the treatment of heparin-induced thrombocy...          ...            
1  Cetuximab, used in combination with irinotecan...          ...            
2  Used as adjunct therapy in the treatment of cy...          ...            
3         For treatment of cutaneous T-cell lymphoma          ...            
4  Etanercept is indicated for the treatment of m...          ...            

  reactions                                        snp-effects  \
0       NaN                                                NaN   
1       NaN  Low affinity immunoglobulin gamma Fc region re...   
2       NaN                                                NaN   
3       NaN                                                NaN   
4       NaN                                                NaN   

  snp-adverse-drug-reactions  \
0                        NaN   
1                        NaN   
2                        NaN   
3                        NaN   
4                        NaN   

                                             targets  \
0  BE0000048ProthrombinHumaninhibitor10505536Turp...   
1  BE0000767Epidermal growth factor receptorHuman...   
2  BE0004796DNAHuman8792953Cramer GW, Bosso JA: T...   
3  BE0000658Interleukin-2 receptor subunit alphaH...   
4  BE0000704Tumor necrosis factorHumanantibody102...   

                                             enzymes carriers transporters  \
0                                                NaN      NaN          NaN   
1                                                NaN      NaN          NaN   
2                                                NaN      NaN          NaN   
3                                                NaN      NaN          NaN   
4  BE0000262Prostaglandin G/H synthase 2Humaninhi...      NaN          NaN   

  average-mass monoisotopic-mass calculated-properties  
0          NaN               NaN                   NaN  
1          NaN               NaN                   NaN  
2          NaN               NaN                   NaN  
3          NaN               NaN                   NaN  
4          NaN               NaN                   NaN  

[5 rows x 55 columns]

In [3]:
df2=df.dropna(subset=['drugname']).reset_index(drop=True)
len(df2)

10661048

In [4]:
df2.to_csv('df2.csv', index=False)

In [6]:
df2.head()

primaryid  drug_seq      caseid                              indi_pt  \
0  100033001         1  10003300.0                         osteoporosis   
1  100033001         1  10003300.0                         osteoporosis   
2  100033062         1  10003306.0  product used for unknown indication   
3  100033072         2  10003307.0           connective tissue disorder   
4  100033083         2  10003308.0                   systemic sclerosis   

   drugname   age  gndr_cod  wt       reporter_country  de  lt  ho  ds  ca  \
0    boniva  77.0       0.0 NaN                     us   0   0   0   1   0   
1    boniva  77.0       0.0 NaN                     us   0   0   0   1   0   
2  letairis  68.0       0.0 NaN                     us   0   0   0   0   0   
3  letairis   NaN       NaN NaN  country not specified   0   0   0   0   0   
4  letairis  59.0       0.0 NaN                     us   0   0   0   0   0   

   ri  ot                 pt drugbank_ID  
0   0   0         arthralgia        None  
1   0   0           headache        None  
2   0   0              cough        None  
3   0   0        rhinorrhoea        None  
4   0   0  unevaluable event        None

In [7]:
df3 = df2.groupby(['drugname'])['drugbank_ID'].size().reset_index()

drugname  drugbank_ID
0                            #4 live transfer factor plus            1
1                                         #7 levofloxacin            2
2                                     'new' ace inhibitor            1
3                                             (abatacept)            5
4       (acetylsalicylic acid) - form : unknown - unit...            1
5                                         (actinomycin d)            6
6                                            (adalimumab)            2
7                                           (alemtuzumab)           24
8                         (alemtuzumab) - unknown - 30 mg            1
9           (alemtuzumab) - unknown - unit dose : unknown            1
10                           (alfuzosin) - tablet - 10 mg            7
11                       (all other therapeutic products)            4
12                                           (amiodarone)            1
13                                (amiodarone) - solution            1
14                 (anthracycline and related substances)            3
15                                           (aprepitant)            3
16                                    (arsenic compounds)            2
17                                         (asparaginase)            1
18                      (astellas) technetium radioactive            3
19                                                 (atra)            5
20                     (azopt) brinzolamide 1% suspension            1
21                                          (bevacizumab)            5
22                            (bupivacaine hydrochloride)            2
23                                             (busulfan)            3
24            (busulphan) - unknown - unit dose : unknown            1
25                                        (c) bm solution           31
26        (calcium chloride w/potassium chlori/06440701/)            3
27                                          (car0oplatin)            1
28                                          (carboplatin)           38
29                                   (cardiac glycosides)            1
...                                                   ...          ...
127860                                             zytrec           17
127861                                           zytrec d            1
127862                                           zytrec-d            1
127863                                             zytrim            2
127864                                              zyvox         2269
127865                                       zyvox 600 mg            2
127866                                     zyvox solution            8
127867    zyvox soultion, sterile (linezolid) (linezolid)            3
127868                                            zyvoxam            6
127869                                            zyvoxid          336
127870     zyvoxid (antibacterials for systemic use) (lo)            2
127871                    zyvoxid (linezolid) (linezolid)            1
127872              zyvoxid (linezolid) solution, sterile            6
127873                         zyvoxid (linezolid) tablet            2
127874                    zyvoxid 600mg (linezolid)tablet            1
127875                    zyvoxid 600mg(linezolid) tablet            1
127876                                     zyvoxid tablet           16
127877                         zyvoxid tablet (linezolid)            4
127878                        zyvoxid tablet (linezolide)            2
127879                                                zyx            3
127880                                     zyx /00052302/            5
127881                                              zyxac            5
127882                                              zyxem            2
127883                                              zyzal            2
127884                                             zyzall            1
12

In [7]:
df.loc[df['drugname'].isnull(), 'drugname']=""

In [8]:
df22=df_drugbank[['drugbank-id', 'products']]
df22.head()

drugbank-id                                           products
0     DB00001  RefludanBayer022409962000-01-312013-07-26Powde...
1     DB00002  ErbituxIm Clone Llc022712492008-10-28Solution2...
2     DB00003  PulmozymeGenentech, Inc.50242-1001993-12-30Sol...
3     DB00004  OntakEisai Limited62856-6032008-10-152017-01-3...
4     DB00005  BrenzysSamsung Bioepis Co., Ltd.024553232016-0...

In [9]:
df.head()

primaryid  drug_seq      caseid                              indi_pt  \
0  100033001         1  10003300.0                         osteoporosis   
1  100033001         1  10003300.0                         osteoporosis   
2  100033061         1  10003306.0  product used for unknown indication   
3  100033062         1  10003306.0  product used for unknown indication   
4  100033072         2  10003307.0           connective tissue disorder   

   drugname   age  gndr_cod  wt       reporter_country  de  lt  ho  ds  ca  \
0    boniva  77.0       0.0 NaN                     us   0   0   0   1   0   
1    boniva  77.0       0.0 NaN                     us   0   0   0   1   0   
2            68.0       0.0 NaN                     us   0   0   0   0   0   
3  letairis  68.0       0.0 NaN                     us   0   0   0   0   0   
4  letairis   NaN       NaN NaN  country not specified   0   0   0   0   0   

   ri  ot           pt drugbank_ID  
0   0   0   arthralgia        None  
1   0   0     headache        None  
2   0   0        cough        None  
3   0   0        cough        None  
4   0   0  rhinorrhoea        None

In [86]:
drug_dict=df22.set_index('drugbank-id').to_dict('index')

In [42]:
drug_dict

{'DB00001': {'products': 'RefludanBayer022409962000-01-312013-07-26Powder, for solution50 mgIntravenousfalsefalsetrueCanadaDPDRefludanCelgene Europe LimitedEMEA/H/C/000122EU/1/97/035/0011997-03-132012-07-27Injection, solution, concentrate50 mgIntravenousfalsefalsefalseEUEMARefludanCelgene Europe LimitedEMEA/H/C/000122EU/1/97/035/0021997-03-132012-07-27Injection, solution, concentrate50 mgIntravenousfalsefalsefalseEUEMARefludanCelgene Europe LimitedEMEA/H/C/000122EU/1/97/035/0031997-03-132012-07-27Injection, solution, concentrate20 mgIntravenousfalsefalsefalseEUEMARefludanCelgene Europe LimitedEMEA/H/C/000122EU/1/97/035/0041997-03-132012-07-27Injection, solution, concentrate20 mgIntravenousfalsefalsefalseEUEMA'},
 'DB00002': {'products': 'ErbituxIm Clone Llc022712492008-10-28Solution2 mgIntravenousfalsefalsetrueCanadaDPDErbituxMerck K Ga AEMEA/H/C/000558EU/1/04/281/0032004-06-29Injection, solution5 mg/mlIntravenousfalsefalsetrueEUEMAErbituxMerck K Ga AEMEA/H/C/000558EU/1/04/281/0052004-

In [14]:
from six import string_types
#isinstance(s, string_types)
isinstance(drug_dict['DB12783']['products'], string_types)

True

In [15]:
def search(myDict, lookup):
    for key, value in myDict.items():
        if isinstance(value['products'], string_types) and lookup in value['products'].lower():
            return str(key)

In [22]:
search(drug_dict, 'letairis')

'DB06403'

In [23]:
len(df2)

10661048

In [24]:
df4=df2.head(10)

In [25]:
df4

primaryid  drug_seq      caseid                                indi_pt  \
0  100033001         1  10003300.0                           osteoporosis   
1  100033001         1  10003300.0                           osteoporosis   
2  100033062         1  10003306.0    product used for unknown indication   
3  100033072         2  10003307.0             connective tissue disorder   
4  100033083         2  10003308.0                     systemic sclerosis   
5  100033093         2  10003309.0                  sleep apnoea syndrome   
6  100033113         1  10003311.0                 pulmonary hypertension   
7  100033113         3  10003311.0                    atrial fibrillation   
8  100033132         2  10003313.0  chronic obstructive pulmonary disease   
9  100033141         1  10003314.0    product used for unknown indication   

   drugname   age  gndr_cod  wt       reporter_country  de  lt  ho  ds  ca  \
0    boniva  77.0       0.0 NaN                     us   0   0   0   1   0   
1    boniva  77.0       0.0 NaN                     us   0   0   0   1   0   
2  letairis  68.0       0.0 NaN                     us   0   0   0   0   0   
3  letairis   NaN       NaN NaN  country not specified   0   0   0   0   0   
4  letairis  59.0       0.0 NaN                     us   0   0   0   0   0   
5  letairis   NaN       NaN NaN  country not specified   0   0   0   0   0   
6  letairis   NaN       NaN NaN  country not specified   0   0   1   0   0   
7  letairis   NaN       NaN NaN  country not specified   0   0   1   0   0   
8  letairis  81.0       0.0 NaN                     us   0   0   0   0   0   
9  letairis   NaN       NaN NaN  country not specified   0   0   0   0   0   

   ri  ot                 pt drugbank_ID  
0   0   0         arthralgia        None  
1   0   0           headache        None  
2   0   0              cough        None  
3   0   0        rhinorrhoea        None  
4   0   0  unevaluable event        None  
5   0   0        no reaction        None  
6   0   0  oedema peripheral        None  
7   0   0  oedema peripheral        None  
8   0   0           jaundice        None  
9   0   0          back pain        None

In [13]:
df4.T.index[6]

'gndr_cod'

In [14]:
for i in df4.iterrows():
    #if i[6]
    print i[1]['drugname']

boniva
boniva

letairis
letairis


letairis

letairis


In [15]:
dict2=[{'boniva':1111}, {'letairis':2222}]

In [9]:
for i,j in df:
    print i,j 

ValueError: too many values to unpack

In [40]:
for index, row in df4.iterrows():
    print row['drugname']

boniva
boniva

letairis
letairis


letairis

letairis


In [26]:
df3=df2.copy()

In [28]:
df3.head()

primaryid  drug_seq      caseid                              indi_pt  \
0  100033001         1  10003300.0                         osteoporosis   
1  100033001         1  10003300.0                         osteoporosis   
2  100033062         1  10003306.0  product used for unknown indication   
3  100033072         2  10003307.0           connective tissue disorder   
4  100033083         2  10003308.0                   systemic sclerosis   

   drugname   age  gndr_cod  wt       reporter_country  de  lt  ho  ds  ca  \
0    boniva  77.0       0.0 NaN                     us   0   0   0   1   0   
1    boniva  77.0       0.0 NaN                     us   0   0   0   1   0   
2  letairis  68.0       0.0 NaN                     us   0   0   0   0   0   
3  letairis   NaN       NaN NaN  country not specified   0   0   0   0   0   
4  letairis  59.0       0.0 NaN                     us   0   0   0   0   0   

   ri  ot                 pt drugbank_ID  
0   0   0         arthralgia        None  
1   0   0           headache        None  
2   0   0              cough        None  
3   0   0        rhinorrhoea        None  
4   0   0  unevaluable event        None

In [55]:
for k,v in drug_dict.items():
    print (v)

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': 'EnBrace HRJaymac Pharmaceuticals, Llc64661-6502015-04-08Capsule, delayed release pelletsOralfalsefalsefalseUSFDA NDCEnLyteJaymac Pharmaceuticals Llc64661-7112011-10-01Capsule, delayed release pelletsOralfalsefalsefalseUSFDA NDC'}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}

{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': 'PyrophosphateAnazao Health Corporation51808-2182012-05-23Injection, powder, lyophilized, for solution27.6 mg/1Intravenousf

{'products': 'AscleraMerz North America, Inc.46783-1212010-06-01Injection, solution.005 g/mLIntravenousNDA021201falsefalsetrueUSFDA NDCAscleraMerz North America, Inc.46783-2212010-06-01Injection, solution.01 g/mLIntravenousNDA021201falsefalsetrueUSFDA NDCVarithenaBiocompatibles, Inc.60635-1182014-07-10KitNDA205098falsefalsetrueUSFDA NDCVarithenaBiocompatibles, Inc.60635-1332013-11-25KitNDA205098falsefalsetrueUSFDA NDCVarithenaProvensis Ltd024442672016-11-30Kit1.3 mgIntravenousfalsefalsetrueCanadaDPDVarithena TMBiocompatibles, Inc.60635-1232014-07-10KitNDA205098falsefalsetrueUSFDA NDC'}
{'products': "3-Step First Aid KitSwabplus Inc.65734-0002003-03-01KitTopicalpart333CfalsetruetrueUSFDA NDC3M Skin and Nasal Antiseptic3 M Pharmaceuticals17518-0602009-07-01Solution5 mg/mLTopicalpart333EfalsetruetrueUSFDA NDCAcu Dyne OintmentAcme United Corporation003991671977-12-311997-05-30Ointment10 %TopicalfalsetruetrueCanadaDPDAcu Dyne Prep Soln LiqAcme United Corporation003936301977-12-311997-05-30L

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




{'products': nan}
{'products': 'AustedoTeva Neuroscience, Inc.68546-1702017-04-12Tablet, coated6 mg/1OralNDA208082falsefalsetrueUSFDA NDCAustedoTeva Neuroscience, Inc.68546-1712017-04-12Tablet, coated9 mg/1OralNDA208082falsefalsetrueUSFDA NDCAustedoTeva Neuroscience, Inc.68546-1722017-04-12Tablet, coated12 mg/1OralNDA208082falsefalsetrueUSFDA NDC'}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}
{'products': nan}


In [71]:
ls='letairis'
import re
for key, value in drug_dict.items():
    if ls in str(value):
        code=key 
    #if str(value['products'])!='nan':
    #    code=re.search('boniva',key)
        print (code)

In [72]:
ls='letairis'
import re
for key, value in drug_dict.items():
    if ls in str(value).lower():
        code=key 
    #if str(value['products'])!='nan':
    #    code=re.search('boniva',key)
        print (code)

DB06403


In [74]:
import re
import time
start = time.time()
j=0
ls='boniva'
for i in range(0,10000):
    #re.search()
    for key, value in drug_dict.items():
        if ls in str(value).lower():
            code=key
            #print (code)
    if j % 1000 == 0:
        now = time.time()
        print (j)
        print (now-start)
    j+= 1

0
0.08796167373657227
1000
78.39679265022278


KeyboardInterrupt: 

In [90]:
import io
import json
with open('dict_drugbank.txt', 'w') as f:
  json.dump(clean_dict,f, ensure_ascii=True)

In [82]:
!pip install simplejson

twisted 18.7.0 requires PyHamcrest>=1.9.0, which is not installed.
You are using pip version 10.0.1, however version 18.0 is available.
You should consider upgrading via the 'python -m pip install --upgrade pip' command.


In [89]:
from collections import OrderedDict
import math
clean_dict = {k: v for k, v in drug_dict.items() if pd.Series(v).notna().all()}

In [83]:
import simplejson

clean_dict  = simplejson.loads(simplejson.dumps(drug_dict, ignore_nan=True))
## or depending on your needs
#clean_dict  = simplejson.loads(simplejson.dumps(my_dict, allow_nan=False))


In [92]:
drug_dict = eval(open("dict_drugbank.txt").read())

In [93]:
import time
start = time.time()
j=0
for index, row in df2.iterrows():
    if (row['drugname'])!="":
        drug_name=row['drugname']
        code=search(drug_dict, drug_name)
        df3.set_value(index,'drugbank_ID',str(code))
        #df4.loc[i,'drugbank_ID']=code
    if j % 1000 == 0:
        now = time.time()
        print (j)
        print (now-start)
    j=j+1

0
5.81763482093811
1000
22.944767713546753
2000
40.06088399887085


KeyboardInterrupt: 

In [94]:
len(df3)

10661048

In [57]:
for i in df.iterrows():
    if (df[1]['drugname'])!="":
        drug_name=df[1]['drugname']
        code=search(drug_dict, drug_name)
        df[1]['drugbank_ID']=code

0
1
3
4
7
9
12
13
15
17
19
20
30
32
33
34
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
93
94
95
96
97
98
99
100
101
102
128
129
130
131
132
133
135
136
137
139
140
143
144
145
146
147
148
149
150
154
155
156
157
158
159
160
161
162
164
178
182
184
185
186
193
197
201
203
205
207
209
210
211
212
213
214
215
218
219
222
224
227
228
233
234
235
236
237
238
239
240
242
244
247
248
249
258
259
263
265
267
269
270
273
275
282
285
286
295
296
297
298
299
300
304
306
308
309
310
313
314
317
319
320
325
326
329
330
331
334
336
338
339
341
342
343
344
345
346
347
349
353
355
356
358
359
362
365
368
370
374
375
376
379
380
383
387
390
391
393
396
398
399
400
401
402
403
404
405
406
417
420
422
423
425
427
428
429
430
431
434
435
436
437
439
440
441
442
443
448
450
451
452
453
454
455
456
457
459
461
463
464
472
481
484
485
486
487
488
489
490
491
494
495
496
497
499
500
501
502
503
504
505
506
507
508
509
510
511
512
513
514
515
516
517
518
519
520
521
522
523
524
525
526
527
52

3515
3516
3517
3518
3519
3520
3521
3522
3523
3524
3525
3528
3530
3531
3532
3534
3541
3542
3543
3544
3545
3546
3547
3549
3550
3551
3552
3553
3554
3555
3556
3557
3558
3559
3560
3561
3562
3563
3564
3565
3566
3569
3570
3571
3572
3573
3576
3577
3578
3579
3580
3581
3582
3583
3585
3586
3587
3588
3589
3590
3591
3592
3593
3594
3595
3596
3597
3598
3599
3600
3601
3606
3609
3610
3612
3613
3614
3615
3620
3621
3622
3630
3631
3632
3633
3634
3635
3636
3637
3638
3650
3651
3652
3653
3654
3655
3656
3657
3658
3659
3660
3661
3662
3663
3664
3665
3666
3667
3668
3669
3670
3671
3672
3673
3674
3675
3676
3677
3678
3679
3680
3681
3682
3683
3684
3685
3686
3687
3688
3689
3690
3691
3692
3693
3694
3695
3696
3697
3698
3699
3700
3701
3702
3703
3704
3705
3706
3707
3708
3709
3710
3711
3712
3713
3714
3715
3716
3717
3718
3719
3720
3721
3722
3723
3724
3725
3726
3727
3728
3729
3730
3731
3732
3733
3734
3735
3736
3737
3738
3739
3740
3741
3742
3743
3744
3745
3746
3747
3748
3749
3750
3751
3759
3760
3761
3762
3763
3764
3765
3766


KeyboardInterrupt: 

In [28]:
df_drugbank['products']=df_drugbank['products'].str.lower()
indx=df_drugbank.loc[df_drugbank['products'].str.contains('letairis')== True].index

In [29]:
df_drugbank.iloc[indx,0]

5593    DB06403
Name: drugbank-id, dtype: object

In [3]:
len(df)

21349480

In [4]:
df2=df.drop(['primaryid', 'drug_seq', 'caseid','de','lt','ho','ds','ca','ri','ot'], axis=1)
df3=df2.dropna().reset_index(drop=True)
len(df3)

2186372

In [5]:
df3['pt'].value_counts()

no reaction                            93677
nausea                                 27596
diarrhoea                              21718
dyspnoea                               21386
fatigue                                21100
drug ineffective                       20987
pain                                   20821
headache                               18411
vomiting                               18377
dizziness                              17976
pyrexia                                17016
pneumonia                              15907
malaise                                14747
asthenia                               14498
weight decreased                       13590
fall                                   13354
anaemia                                12783
arthralgia                             12742
anxiety                                12405
pain in extremity                      12349
insomnia                               12116
depression                             11448
abdominal 

In [12]:
df_f=df[df['pt']=='nausea']
df_f['drugname'].value_counts()

humira                                    1753
byetta                                    1633
cymbalta                                  1291
chantix                                   1286
enbrel                                    1278
tecfidera                                 1237
otezla                                    1033
forteo                                     968
pegasys                                    801
lyrica                                     670
remicade                                   638
ribavirin                                  619
tysabri                                    609
nexium                                     602
methotrexate                               598
fosamax                                    564
xyrem                                      546
avonex                                     528
victoza                                    505
yaz                                        496
synthroid                                  492
metformin    

In [5]:
common_drugs=df3['drugname'].value_counts().index[:11]

In [6]:
df4=df3[df3['drugname'].isin(common_drugs)]

In [7]:
df4.head()

indi_pt  drugname    age  gndr_cod    wt  \
117  ankylosing spondylitis    humira  61.29       1.0  75.0   
118  ankylosing spondylitis    humira  61.29       1.0  75.0   
218   anticoagulant therapy   aspirin  52.00       0.0  75.0   
219   anticoagulant therapy   aspirin  52.00       0.0  75.0   
238         crohn's disease  remicade  66.45       0.0  58.8   

          reporter_country                             pt  
117  country not specified                     cold sweat  
118  country not specified                   palpitations  
218                     br  arteriogram coronary abnormal  
219                     br               weight decreased  
238                     ca                    no reaction

In [9]:
df4.drugname.value_counts()

vioxx           29125
fosamax         28209
seroquel        26972
humira          26151
lyrica          20558
nexium          18692
remicade        16261
zometa          13371
aspirin         11171
lipitor         11020
methotrexate    10535
Name: drugname, dtype: int64

In [9]:
len(df4)

212065

df4['pub_ID']=0.0
df4.loc[df4['drugname']=='vioxx', 'pub_ID']=5090
df4.loc[df4['drugname']=='fosamax', 'pub_ID']=2088
df4.loc[df4['drugname']=='seroquel', 'pub_ID']=5002
df4.loc[df4['drugname']=='humira', 'pub_ID']=107706
df4.loc[df4['drugname']=='lyrica', 'pub_ID']=5486971
df4.loc[df4['drugname']=='nexium', 'pub_ID']=4594
df4.loc[df4['drugname']=='zometa', 'pub_ID']=68740
df4.loc[df4['drugname']=='aspirin', 'pub_ID']=2244
df4.loc[df4['drugname']=='lipitor', 'pub_ID']=60822
df4.loc[df4['drugname']=='methotrexate', 'pub_ID']=126941
df4=df4[df4['pub_ID']!=0].reset_index(drop=True)
len(df4)

In [10]:
df4['drugbank_ID']=0.0
df4.loc[df4['drugname']=='vioxx', 'drugbank_ID']='DB00533'
df4.loc[df4['drugname']=='fosamax', 'drugbank_ID']='DB00630'
df4.loc[df4['drugname']=='seroquel', 'drugbank_ID']='DB01224'
df4.loc[df4['drugname']=='humira', 'drugbank_ID']='DB00051'
df4.loc[df4['drugname']=='lyrica', 'drugbank_ID']='DB00230'
df4.loc[df4['drugname']=='nexium', 'drugbank_ID']='DB00736'
df4.loc[df4['drugname']=='zometa', 'drugbank_ID']='DB00399'
df4.loc[df4['drugname']=='aspirin', 'drugbank_ID']='DB00945'
df4.loc[df4['drugname']=='lipitor', 'drugbank_ID']='DB01076'
df4.loc[df4['drugname']=='methotrexate', 'drugbank_ID']='DB00563'
df4.loc[df4['drugname']=='remicade', 'drugbank_ID']='DB00065'
len(df4)

212065

In [12]:
df4.head()

indi_pt  drugname    age  gndr_cod    wt  \
117  ankylosing spondylitis    humira  61.29       1.0  75.0   
118  ankylosing spondylitis    humira  61.29       1.0  75.0   
218   anticoagulant therapy   aspirin  52.00       0.0  75.0   
219   anticoagulant therapy   aspirin  52.00       0.0  75.0   
238         crohn's disease  remicade  66.45       0.0  58.8   

          reporter_country                             pt drugbank_ID  
117  country not specified                     cold sweat     DB00051  
118  country not specified                   palpitations     DB00051  
218                     br  arteriogram coronary abnormal     DB00945  
219                     br               weight decreased     DB00945  
238                     ca                    no reaction     DB00065

In [21]:
#print (df4['drugbank_ID'].values)
print(*df4['drugbank_ID'].unique(), sep='\n')

DB00051
DB00945
DB00065
DB01076
DB00563
DB00399
DB00230
DB00630
DB00736
DB01224
DB00533


In [23]:
drug_sel=pd.read_csv('drug_sel.csv')
drug_sel.head()

drugbank-id             name  \
0     DB00051       Adalimumab   
1     DB00065       Infliximab   
2     DB00230       Pregabalin   
3     DB00399  Zoledronic acid   
4     DB00533        Rofecoxib   

                                         description   cas-number        unii  \
0  Adalimumab is a human monoclonal antibody agai...  331731-18-1  FYS6T7F842   
1  Infliximab is a tumor necrosis factor (TNF-alp...  170277-31-3  B72HH48FLU   
2  Pregabalin is an anticonvulsant drug used for ...  148553-50-8  55JG375S6M   
3  Zoledronate (zoledronic acid, marketed by Nova...  118072-93-8  70HZ18PH24   
4  Rofecoxib is used for the treatment of osteoar...  162011-90-7  0QTW8Z7MCR   

    state                            groups  \
0  liquid                          approved   
1  liquid                          approved   
2   solid    approvedillicitinvestigational   
3   solid                          approved   
4   solid  approvedinvestigationalwithdrawn   

                                  general-references  \
0  Linkhttp://www.freepatentsonline.com/6090382.h...   
1  10228190Present DH, Rutgeerts P, Targan S, Han...   
2  16050051Authors unspecified: Schedules of cont...   
3  17878149Lyles KW, Colon-Emeric CS, Magaziner J...   
4  11087881Bombardier C, Laine L, Reicin A, Shapi...   

                                 synthesis-reference  \
0                                                NaN   
1                                                NaN   
2  Mark Burk, "Asymmetric synthesis of pregabalin...   
3  Judith Aronhime, Revital Lifshitz-Liron, "Zole...   
4                                                NaN   

                                          indication  \
0  For treatment of rheumatoid arthritis, psoriat...   
1  * Indicated for reducing signs and symptoms an...   
2  Pregabalin is used for the management of neuro...   
3  For the treatment of hypercalcemia of malignan...   
4  For the treatment of osteoarthritis, rheumatoi...   

                         ...                          \
0                        ...                           
1                        ...                           
2                        ...                           
3                        ...                           
4                        ...                           

                                           reactions  \
0                                                NaN   
1                                                NaN   
2     1DB00230PregabalinDBMET01540N-methylpregabalin   
3                                                NaN   
4  1DB00533RofecoxibDBMET001695-HydroxyrofecoxibB...   

                                         snp-effects  \
0                                                NaN   
1  Low affinity immunoglobulin gamma Fc region re...   
2                                                NaN   
3                                                NaN   
4                                                NaN   

  snp-adverse-drug-reactions  \
0                        NaN   
1                        NaN   
2                        NaN   
3                        NaN   
4                        NaN   

                                             targets  \
0  BE0000704Tumor necrosis factorHumanantibody120...   
1  BE0000704Tumor necrosis factorHumaninhibitor11...   
2  BE0000356Voltage-dependent P/Q-type calcium ch...   
3  BE0000776Farnesyl pyrophosphate synthaseHumani...   
4  BE0000262Prostaglandin G/H synthase 2Humaninhi...   

                                             enzymes carriers  \
0                                                NaN      NaN   
1                                                NaN      NaN   
2                                                NaN      NaN   
3                                                NaN      NaN   
4  BE0002433Cytochrome P450 1A2Humansubstrateinhi...      NaN   

                                        transporters average-mass  \
0              

In [24]:
dd=drug_sel[['drugbank-id','name','protein-binding','pathways','targets','enzymes','average-mass','calculated-properties']]
dd.head()

drugbank-id             name  \
0     DB00051       Adalimumab   
1     DB00065       Infliximab   
2     DB00230       Pregabalin   
3     DB00399  Zoledronic acid   
4     DB00533        Rofecoxib   

                                     protein-binding  \
0                                                NaN   
1                                                NaN   
2  Pregabalin does not bind to plasma proteins.[F...   
3  Approximately 22% bound in human plasma, indep...   
4                                                87%   

                                            pathways  \
0                                                NaN   
1                                                NaN   
2                                                NaN   
3  SMP00107Zoledronate Action Pathwaydrug_actionD...   
4  SMP00087Rofecoxib Action Pathwaydrug_actionDB0...   

                                             targets  \
0  BE0000704Tumor necrosis factorHumanantibody120...   
1  BE0000704Tumor necrosis factorHumaninhibitor11...   
2  BE0000356Voltage-dependent P/Q-type calcium ch...   
3  BE0000776Farnesyl pyrophosphate synthaseHumani...   
4  BE0000262Prostaglandin G/H synthase 2Humaninhi...   

                                             enzymes  average-mass  \
0                                                NaN           NaN   
1                                                NaN           NaN   
2                                                NaN      159.2261   
3                                                NaN      272.0896   
4  BE0002433Cytochrome P450 1A2Humansubstrateinhi...      314.3560   

                               calculated-properties  
0                                                NaN  
1                                                NaN  
2  logP-1.4ALOGPSlogS-1.2ALOGPSWater Solubility1....  
3  logP-0.93ALOGPSlogS-1.9ALOGPSWater Solubility3...  
4  logP2.32ALOGPSlogS-4.5ALOGPSWater Solubility1....

In [27]:
dd.to_excel('dd.xlsx', index=False)

In [13]:
df4['pt'].value_counts()

no reaction                                4710
drug ineffective                           2147
pain                                       2142
fatigue                                    1550
myocardial infarction                      1539
fall                                       1515
arthralgia                                 1509
pain in extremity                          1498
hypertension                               1491
nausea                                     1489
dizziness                                  1489
insomnia                                   1460
depression                                 1433
anxiety                                    1408
malaise                                    1386
headache                                   1374
dyspnoea                                   1340
drug dose omission                         1333
chest pain                                 1327
gastrooesophageal reflux disease           1245
diarrhoea                               

In [14]:
df4['myocardial_infarction']=0.0
df4.loc[df4['pt']=='myocardial infarction', 'myocardial_infarction'] = 1.0
df4.head()

indi_pt drugname    age  gndr_cod    wt  \
0             ankylosing spondylitis   humira  61.29       1.0  75.0   
1             ankylosing spondylitis   humira  61.29       1.0  75.0   
2              anticoagulant therapy  aspirin  52.00       0.0  75.0   
3              anticoagulant therapy  aspirin  52.00       0.0  75.0   
4  low density lipoprotein increased  lipitor  49.00       0.0  77.0   

        reporter_country                             pt    pub_ID  \
0  country not specified                     cold sweat  107706.0   
1  country not specified                   palpitations  107706.0   
2                     br  arteriogram coronary abnormal    2244.0   
3                     br               weight decreased    2244.0   
4                     us                    no reaction   60822.0   

   myocardial_infarction  
0                    0.0  
1                    0.0  
2                    0.0  
3                    0.0  
4                    0.0

In [16]:
dummy_col = pd.get_dummies(df4[['drugname','reporter_country','indi_pt']])
df5=df4.drop(['indi_pt','drugname','reporter_country','pt','pub_ID'] , axis=1)
df5 = pd.concat([df5, dummy_col], axis=1)
df5.head()

age  gndr_cod    wt  myocardial_infarction  drugname_aspirin  \
0  61.29       1.0  75.0                    0.0                 0   
1  61.29       1.0  75.0                    0.0                 0   
2  52.00       0.0  75.0                    0.0                 1   
3  52.00       0.0  75.0                    0.0                 1   
4  49.00       0.0  77.0                    0.0                 0   

   drugname_fosamax  drugname_humira  drugname_lipitor  drugname_lyrica  \
0                 0                1                 0                0   
1                 0                1                 0                0   
2                 0                0                 0                0   
3                 0                0                 0                0   
4                 0                0                 1                0   

   drugname_methotrexate          ...            indi_pt_vomiting  \
0                      0          ...                           0   
1                      0          ...                           0   
2                      0          ...                           0   
3                      0          ...                           0   
4                      0          ...                           0   

   indi_pt_vulvitis  indi_pt_vulvovaginal pain  indi_pt_vulvovaginal pruritus  \
0                 0                          0                              0   
1                 0                          0                              0   
2                 0                          0                              0   
3                 0                          0                              0   
4                 0                          0                              0   

   indi_pt_weakness in extremity  indi_pt_wegener's granulomatosis  \
0                              0                                 0   
1                              0                                 0   
2                              0                                 0   
3                              0                                 0   
4                              0                                 0   

   indi_pt_weight increased  indi_pt_whiplash injury  indi_pt_wrist fracture  \
0                         0                        0                       0   
1                         0                        0                       0   
2                         0                        0                       0   
3                         0                        0                       0   
4                         0                        0                       0   

   indi_pt_wrist surgery  
0                      0  
1                      0  
2                      0  
3                      0  
4                      0  

[5 rows x 1335 columns]

In [21]:
y=df5['myocardial_infarction']
X=df5.drop(['myocardial_infarction'], axis=1)
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.1, random_state=0, stratify=y)
clf1 = RandomForestClassifier(n_estimators=100, class_weight='balanced', n_jobs=-1, random_state=0, oob_score=True)    #building 50 decision trees
clf1.fit(X_train, y_train)
print("myocardial_infarction(pt) model")
print("oob score:"), clf1.oob_score_
print (metrics.accuracy_score(y_test, clf1.predict(X_test)))

print (metrics.confusion_matrix(y_test, clf1.predict(X_test)))
print ("=======================================================")

myocardial_infarction(pt) model
oob score:
0.9462233798069557
[[18505   922]
 [  131    23]]


In [23]:
lr= LogisticRegression(class_weight='balanced')
lr.fit(X_train, y_train)
print (metrics.accuracy_score(y_test, lr.predict(X_test)))
print (metrics.confusion_matrix(y_test, lr.predict(X_test)))
print (metrics.classification_report(y_test, lr.predict(X_test)))
print (metrics.roc_auc_score(y_test, lr.predict(X_test)))

0.809560288034319
[[15740  3687]
 [   42   112]]
             precision    recall  f1-score   support

        0.0       1.00      0.81      0.89     19427
        1.0       0.03      0.73      0.06       154

avg / total       0.99      0.81      0.89     19581

0.7687426589984886


In [15]:
df_xa=pd.read_csv('xarelto_interactions.tsv', sep="\t")
df_xa.head()

#node1        node2  node1_string_internal_id  node2_string_internal_id  \
0  VPS36       TSG101                   1856803                   1844091   
1    F10  rivaroxaban                   1856330                  -9875401   
2    F10           F3                   1856330                   1851684   
3  CHMP3        VPS36                   1860537                   1856803   
4  CHMP3       TSG101                   1860537                   1844091   

      node1_external_id     node2_external_id  neighborhood_on_chromosome  \
0  9606.ENSP00000367299  9606.ENSP00000251968                           0   
1  9606.ENSP00000364709       -1.CID009875401                           0   
2  9606.ENSP00000364709  9606.ENSP00000334145                           0   
3  9606.ENSP00000405575  9606.ENSP00000367299                           0   
4  9606.ENSP00000405575  9606.ENSP00000251968                           0   

   gene_fusion  phylogenetic_cooccurrence  homology  coexpression  \
0            0                          0         0           0.0   
1            0                          0         0           0.0   
2            0                          0         0           0.0   
3            0                          0         0           0.0   
4            0                          0         0           0.0   

   experimentally_determined_interaction  database_annotated  \
0                                  0.937                 0.9   
1                                  0.854                 0.8   
2                                  0.917                 0.9   
3                                  0.292                 0.9   
4                                  0.300                 0.9   

   automated_textmining  prediction  combined_score  
0                 0.872           0           0.999  
1                 0.928           0           0.997  
2                 0.345           0           0.994  
3                 0.878           0           0.990  
4                 0.867           0           0.989

In [4]:
df_art=df[df['indi_pt']=='rheumatoid arthritis'].drop(['indi_pt','primaryid','drug_seq','caseid'], axis=1).dropna().reset_index(drop=True)
df_art.head()

drugname   age  gndr_cod     wt reporter_country  de  lt  ho  ds  ca  \
0       xeljanz  66.0       0.0  48.07               us   0   0   0   0   0   
1       xeljanz  66.0       0.0  48.07               us   0   0   0   0   0   
2       xeljanz  66.0       0.0  48.07               us   0   0   0   0   0   
3  methotrexate  55.0       0.0  67.00               br   0   0   0   0   0   
4  methotrexate  55.0       0.0  67.00               br   0   0   0   0   0   

   ri  ot                    pt  
0   0   0  abdominal discomfort  
1   0   0    decreased appetite  
2   0   0     pain in extremity  
3   0   0              headache  
4   0   0              pruritus

In [5]:
len(df_art)

54862

In [38]:
df_art['pt'].value_counts()

no reaction                         3155
arthralgia                           916
rheumatoid arthritis                 793
drug ineffective                     742
pain                                 679
pneumonia                            603
fatigue                              501
pain in extremity                    488
nausea                               481
headache                             478
dyspnoea                             452
fall                                 437
pyrexia                              418
injection site pain                  386
weight decreased                     385
cough                                383
diarrhoea                            361
nasopharyngitis                      355
joint swelling                       354
malaise                              348
dizziness                            335
vomiting                             314
hypertension                         295
urinary tract infection              293
weight increased

In [6]:
df_art['pneumonia']=0.0
df_art.loc[df_art['pt']=='pneumonia', 'pneumonia'] = 1.0
df_art.head()

drugname   age  gndr_cod     wt reporter_country  de  lt  ho  ds  ca  \
0       xeljanz  66.0       0.0  48.07               us   0   0   0   0   0   
1       xeljanz  66.0       0.0  48.07               us   0   0   0   0   0   
2       xeljanz  66.0       0.0  48.07               us   0   0   0   0   0   
3  methotrexate  55.0       0.0  67.00               br   0   0   0   0   0   
4  methotrexate  55.0       0.0  67.00               br   0   0   0   0   0   

   ri  ot                    pt  pneumonia  
0   0   0  abdominal discomfort        0.0  
1   0   0    decreased appetite        0.0  
2   0   0     pain in extremity        0.0  
3   0   0              headache        0.0  
4   0   0              pruritus        0.0

In [7]:
dummy_col = pd.get_dummies(df_art[['drugname','gndr_cod','reporter_country']])
df_art=df_art.drop(['drugname','gndr_cod','reporter_country','pt'] , axis=1)
df_art = pd.concat([df_art, dummy_col], axis=1)
df_art.head()

age     wt  de  lt  ho  ds  ca  ri  ot  pneumonia         ...           \
0  66.0  48.07   0   0   0   0   0   0   0        0.0         ...            
1  66.0  48.07   0   0   0   0   0   0   0        0.0         ...            
2  66.0  48.07   0   0   0   0   0   0   0        0.0         ...            
3  55.0  67.00   0   0   0   0   0   0   0        0.0         ...            
4  55.0  67.00   0   0   0   0   0   0   0        0.0         ...            

   reporter_country_tw  reporter_country_ua  reporter_country_ukraine  \
0                    0                    0                         0   
1                    0                    0                         0   
2                    0                    0                         0   
3                    0                    0                         0   
4                    0                    0                         0   

   reporter_country_united arab emirates  reporter_country_us  \
0                                      0                    1   
1                                      0                    1   
2                                      0                    1   
3                                      0                    0   
4                                      0                    0   

   reporter_country_us minor outlying islands  reporter_country_uy  \
0                                           0                    0   
1                                           0                    0   
2                                           0                    0   
3                                           0                    0   
4                                           0                    0   

   reporter_country_ve  reporter_country_venezuela  reporter_country_za  
0                    0                           0                    0  
1                    0                           0                    0  
2                    0                           0                    0  
3                    0                           0                    0  
4                    0                           0                    0  

[5 rows x 1250 columns]

In [8]:
y=df_art['pneumonia']
X=df_art.drop(['de','lt','ho','ds','ca','ri','ot','pneumonia'], axis=1)
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.1, random_state=0, stratify=y)
clf1 = RandomForestClassifier(n_estimators=100, class_weight='balanced', n_jobs=-1, random_state=0, oob_score=True)    #building 50 decision trees
clf1.fit(X_train, y_train)
print "pneumonia(pt) model in arthritis(disease)"
print "oob score:", clf1.oob_score_
print metrics.accuracy_score(y_test, clf1.predict(X_test))

print metrics.confusion_matrix(y_test, clf1.predict(X_test))
print "======================================================="

pneumonia(pt) model in arthritis(disease)
oob score: 0.9548759493670886
0.9542555130308
[[5231  196]
 [  55    5]]


In [9]:
y.value_counts()

0.0    54259
1.0      603
Name: pneumonia, dtype: int64

In [ ]:
svc = svm.SVC(kernel='linear', class_weight='balanced', C=1.0, random_state=0)
svc.fit(X_train, y_train)
print metrics.accuracy_score(y_test, svc.predict(X_test))
print metrics.confusion_matrix(y_test, svc.predict(X_test))

In [10]:
lr= LogisticRegression(class_weight='balanced')
lr.fit(X_train, y_train)
print metrics.accuracy_score(y_test, lr.predict(X_test))
print metrics.confusion_matrix(y_test, lr.predict(X_test))
print metrics.classification_report(y_test, lr.predict(X_test))
print metrics.roc_auc_score(y_test, lr.predict(X_test))

0.7173318753417168
[[3901 1526]
 [  25   35]]
             precision    recall  f1-score   support

        0.0       0.99      0.72      0.83      5427
        1.0       0.02      0.58      0.04        60

avg / total       0.98      0.72      0.83      5487

0.6510733370186107


In [11]:
from imblearn.under_sampling import (ClusterCentroids, RandomUnderSampler,
                                     NearMiss,
                                     InstanceHardnessThreshold,
                                     CondensedNearestNeighbour,
                                     EditedNearestNeighbours,
                                     RepeatedEditedNearestNeighbours,
                                     AllKNN,
                                     NeighbourhoodCleaningRule,
                                     OneSidedSelection)

In [13]:
from collections import Counter
Counter(y_train)

Counter({0.0: 48832, 1.0: 543})

In [14]:
from imblearn.under_sampling import TomekLinks
from imblearn.under_sampling import ClusterCentroids
cc = ClusterCentroids(random_state=0)
ru=RandomUnderSampler(random_state=0)
X_resampled, y_resampled = ru.fit_sample(X_train, y_train)
#X_train_res, X_test_res, y_train_res, y_test_res = train_test_split(X_resampled, y_resampled, test_size=0.1, random_state=0, stratify=y)
clf2 = RandomForestClassifier(n_estimators=100, class_weight='balanced', n_jobs=-1, random_state=0, oob_score=True)    #building 50 decision trees
clf2.fit(X_resampled, y_resampled)
print "pneumonia(pt) model in arthritis(disease) (UNDERSAMPLING)"
print "oob score:", clf2.oob_score_
print metrics.accuracy_score(y_test, clf2.predict(X_test))

print metrics.confusion_matrix(y_test, clf2.predict(X_test))

pneumonia(pt) model in arthritis(disease) (UNDERSAMPLING)
oob score: 0.5883977900552486
0.5924913431747767
[[3205 2222]
 [  14   46]]


In [15]:
lr= LogisticRegression(class_weight='balanced')
lr.fit(X_resampled, y_resampled)
print "pneumonia(pt) model in arthritis(disease) (UNDERSAMPLING)-LogisticRegression"
print metrics.accuracy_score(y_test, lr.predict(X_test))

print metrics.confusion_matrix(y_test, lr.predict(X_test))

pneumonia(pt) model in arthritis(disease) (UNDERSAMPLING)-LogisticRegression
0.6001457991616548
[[3251 2176]
 [  18   42]]


In [72]:
from collections import Counter
Counter(y_resampled)

Counter({0.0: 543, 1.0: 543})

In [16]:
from imblearn.over_sampling import SMOTE  
#imblearn.over_sampling.SMOTE
sme = SMOTE(random_state=42)
X_res, y_res = sme.fit_sample(X_train, y_train)
clf3 = RandomForestClassifier(n_estimators=100, class_weight='balanced', n_jobs=-1, random_state=0, oob_score=True)    #building 50 decision trees
clf3.fit(X_res, y_res)
print "pneumonia(pt) model in arthritis(disease)(OVERSAMPLING)"
print "oob score:", clf3.oob_score_
print metrics.accuracy_score(y_test, clf3.predict(X_test))

print metrics.confusion_matrix(y_test, clf3.predict(X_test))

pneumonia(pt) model in arthritis(disease)(OVERSAMPLING)
oob score: 0.9898017693315858
0.9834153453617641
[[5395   32]
 [  59    1]]


In [18]:
lr= LogisticRegression(class_weight='balanced')
lr.fit(X_res, y_res)
print "pneumonia(pt) model in arthritis(disease) (OVERSAMPLING)-LogisticRegression"
print metrics.accuracy_score(y_test, lr.predict(X_test))

print metrics.confusion_matrix(y_test, lr.predict(X_test))

pneumonia(pt) model in arthritis(disease) (OVERSAMPLING)-LogisticRegression
0.764898851831602
[[4166 1261]
 [  29   31]]


In [76]:
Counter(y_res)

Counter({0.0: 48832, 1.0: 48832})

In [19]:
df_art.corr()['pneumonia'].sort_values()

reporter_country_us                         -0.020129
wt                                          -0.017778
drugname_enbrel                             -0.013444
reporter_country_fr                         -0.012555
ot                                          -0.010589
drugname_mabthera                           -0.008457
drugname_humira                             -0.007938
drugname_actemra                            -0.007899
reporter_country_ca                         -0.007303
drugname_rituxan                            -0.007182
ds                                          -0.007181
drugname_arava                              -0.006908
drugname_remicade                           -0.006751
drugname_sulfasalazine.                     -0.006735
drugname_folic acid.                        -0.006050
reporter_country_mx                         -0.005922
drugname_humira 40 mg/0.8 ml pen            -0.005611
drugname_fosamax                            -0.005483
reporter_country_br         

In [31]:
c1 = core.unstack()
c1.sort_values(ascending = False)

pt_zika virus infection                        pt_zika virus infection                          1.000000
pt_malignant neoplasm progression              pt_malignant neoplasm progression                1.000000
pt_marrow hyperplasia                          pt_marrow hyperplasia                            1.000000
pt_mantle cell lymphoma                        pt_mantle cell lymphoma                          1.000000
pt_mania                                       pt_mania                                         1.000000
pt_mammoplasty                                 pt_mammoplasty                                   1.000000
pt_mammogram abnormal                          pt_mammogram abnormal                            1.000000
pt_malnutrition                                pt_malnutrition                                  1.000000
pt_malignant pleural effusion                  pt_malignant pleural effusion                    1.000000
pt_malignant neoplasm of unknown primary site  pt_malig

In [32]:
pd.DataFrame(c1)[pd.DataFrame(c1)[0]<1].sort_values([0], ascending=False)

0
drugname_calcium d3 stada               pt_oropharyngeal cancer                  0.707100
pt_oropharyngeal cancer                 drugname_calcium d3 stada                0.707100
drugname_solu-dacortin                  pt_hypereosinophilic syndrome            0.707100
pt_hypereosinophilic syndrome           drugname_solu-dacortin                   0.707100
pt_demyelinating polyneuropathy         drugname_coxflam                         0.707100
drugname_coxflam                        pt_demyelinating polyneuropathy          0.707100
pt_pancreatic carcinoma metastatic      drugname_percocet                        0.707100
drugname_percocet                       pt_pancreatic carcinoma metastatic       0.707100
pt_restrictive pulmonary disease        drugname_nexen                           0.707100
drugname_nexen                          pt_restrictive pulmonary disease         0.707100
drugname_ambrisentan                    pt_acute left ventricular failure        0.707100
pt_acute left ventricular failure       drugname_ambrisentan                     0.707100
pt_small intestinal perforation         drugname_amaryl                          0.707100
                                        drugname_thyradin-s                      0.707100
drugname_thyradin-s                     pt_small intestinal perforation          0.707100
drugname_amaryl                         pt_small intestinal perforation          0.707100
pt_vestibular disorder                  drugname_hct                             0.707100
drugname_hct                            pt_vestibular disorder                   0.707100
drugname_metypred//methylprednisolone   pt_tongue oedema                         0.707100
pt_tongue oedema                        drugname_metypred//methylprednisolone    0.707100
drugname_tolmetin                       pt_psychomotor hyperactivity             0.707100
pt_psychomotor hyperactivity            drugname_tolmetin                        0.707100
drugname_olfen                          pt_anogenital warts                      0.577340
pt_anogenital warts                     drugname_olfen                           0.577340
pt_legionella serology positive         drugname_imurel                          0.577340
drugname_imurel                         pt_legionella serology positive          0.577340
drugname_plaquenil /00072601/           pt_atrial thrombosis                     0.577340
pt_atrial thrombosis                    drugname_plaquenil /00072601/            0.577340
drugname_enbrel 25mg for s.c. injection pt_cytomegalovirus viraemia              0.577340
pt_cytomegalovirus viraemia             drugname_enbrel 25mg for s.c. injection  0.577340
...                                                                                   ...
wt                                      drugname_rheumatrex                     -0.079187
drugname_rheumatrex                     wt                                      -0.079187
drugname_enbrel                         drugname_actemra                        -0.080758
drugname_actemra                        drugname_enbrel                         -0.080758
ho                                      drugname_enbrel                         -0.081946
drugname_enbrel                         ho                                      -0.081946
ot                                      lt                                      -0.083473
lt                                      ot                                      -0.083473
drugname_methotrexate                   drugname_actemra                        -0.084473
drugname_actemra                        drugname_methotrexate                   -0.084473
drugname_rituxan                        drugname_humira                         -0.084857
drugname_humira                         drugname_rituxan                        -0.084857
drugname_enbrel                         drugname_methotrexate                   -0.084886
drugname_methotrexate                 

In [49]:
df_art.head()

age     wt  de  lt  ho  ds  ca  ri  ot  arthralgia         ...           \
0  66.0  48.07   0   0   0   0   0   0   0         0.0         ...            
1  66.0  48.07   0   0   0   0   0   0   0         0.0         ...            
2  66.0  48.07   0   0   0   0   0   0   0         0.0         ...            
3  55.0  67.00   0   0   0   0   0   0   0         0.0         ...            
4  55.0  67.00   0   0   0   0   0   0   0         0.0         ...            

   reporter_country_tw  reporter_country_ua  reporter_country_ukraine  \
0                    0                    0                         0   
1                    0                    0                         0   
2                    0                    0                         0   
3                    0                    0                         0   
4                    0                    0                         0   

   reporter_country_united arab emirates  reporter_country_us  \
0                                      0                    1   
1                                      0                    1   
2                                      0                    1   
3                                      0                    0   
4                                      0                    0   

   reporter_country_us minor outlying islands  reporter_country_uy  \
0                                           0                    0   
1                                           0                    0   
2                                           0                    0   
3                                           0                    0   
4                                           0                    0   

   reporter_country_ve  reporter_country_venezuela  reporter_country_za  
0                    0                           0                    0  
1                    0                           0                    0  
2                    0                           0                    0  
3                    0                           0                    0  
4                    0                           0                    0  

[5 rows x 1250 columns]